In [257]:
from pandas.io.json import json_normalize #package for flattening json in pandas df
from pathlib import Path
import pandas as pd
import json
import os 

#function to convert json data to pandas df 
def createDF(json_data):
    json_df = json_normalize(json_data['data'],record_path=['birds'],sep="_")
    time_stamp = datetime.datetime.strptime(json_data['timestamp'], '%d-%b-%Y %H:%M:%S.%f')
    #time_stamp = json_data['timestamp']
    bird = pd.concat([json_df.drop(['location'], axis=1), json_df['location'].apply(pd.Series)], axis=1)
    bird['timestamp'] = time_stamp
    return bird

In [258]:
# def createCSV():

pathlist = Path("./bird-view/responses").glob('**/*.json') # return path object 
bird_data_list = []
for path in pathlist:
    path_in_str = str(path)
    with open(path_in_str) as f:
        json_f_data = json.load(f)
        try:
            json_bird_df = createDF(json_f_data)
            json_bird_df = json_bird_df.rename(columns = {'id':'bird_id'})
            clean_bird_df = json_bird_df.drop(columns=['captive', 'code'])
            bird_data_list.append(clean_bird_df)
        except ValueError: # no data for scooters, scooters are offline 
            continue
bird_data = pd.concat(bird_data_list, axis=0)
print(bird_data.head())
print("Completed!")

   battery_level                               bird_id nest_id   latitude  \
0             63  3ffc1a8b-a939-4db4-82fa-bd44ee18d3a4     NaN  34.024452   
1             60  6137c185-4c43-4a4f-8c9c-d1be75954d4a     NaN  34.024452   
2             93  b97c8605-a3e9-4d9d-a440-1fe96dedf1e2     NaN  34.024899   
3             92  da84d4b4-d3a6-405b-8fef-21c04f31ca74     NaN  34.024967   
4             76  29b37932-e2db-41b6-a117-355b14d3791e     NaN  34.025077   

    longitude                  timestamp  
0 -118.497017 2019-06-11 22:15:02.035402  
1 -118.497200 2019-06-11 22:15:02.035402  
2 -118.496032 2019-06-11 22:15:02.035402  
3 -118.496048 2019-06-11 22:15:02.035402  
4 -118.496020 2019-06-11 22:15:02.035402  
Completed!


In [259]:
bird_data.head()


battery_level                               bird_id nest_id   latitude  \
0             63  3ffc1a8b-a939-4db4-82fa-bd44ee18d3a4     NaN  34.024452   
1             60  6137c185-4c43-4a4f-8c9c-d1be75954d4a     NaN  34.024452   
2             93  b97c8605-a3e9-4d9d-a440-1fe96dedf1e2     NaN  34.024899   
3             92  da84d4b4-d3a6-405b-8fef-21c04f31ca74     NaN  34.024967   
4             76  29b37932-e2db-41b6-a117-355b14d3791e     NaN  34.025077   

    longitude                  timestamp  
0 -118.497017 2019-06-11 22:15:02.035402  
1 -118.497200 2019-06-11 22:15:02.035402  
2 -118.496032 2019-06-11 22:15:02.035402  
3 -118.496048 2019-06-11 22:15:02.035402  
4 -118.496020 2019-06-11 22:15:02.035402

In [260]:
len(bird_data.bird_id.unique()) # 502 unique birds 

1429

In [261]:
import folium

bird_data.timestamp = pd.to_datetime(bird_data.timestamp, format='%Y-%m-%d %H:%M:%S')
bird_data['month'] = bird_data.timestamp.apply(lambda x: x.month)
bird_data['week'] = bird_data.timestamp.apply(lambda x: x.week)
bird_data['day'] = bird_data.timestamp.apply(lambda x: x.day)
bird_data['hour'] = bird_data.timestamp.apply(lambda x: x.hour)

In [262]:
bird_data.head()

battery_level                               bird_id nest_id   latitude  \
0             63  3ffc1a8b-a939-4db4-82fa-bd44ee18d3a4     NaN  34.024452   
1             60  6137c185-4c43-4a4f-8c9c-d1be75954d4a     NaN  34.024452   
2             93  b97c8605-a3e9-4d9d-a440-1fe96dedf1e2     NaN  34.024899   
3             92  da84d4b4-d3a6-405b-8fef-21c04f31ca74     NaN  34.024967   
4             76  29b37932-e2db-41b6-a117-355b14d3791e     NaN  34.025077   

    longitude                  timestamp  month  week  day  hour  
0 -118.497017 2019-06-11 22:15:02.035402      6    24   11    22  
1 -118.497200 2019-06-11 22:15:02.035402      6    24   11    22  
2 -118.496032 2019-06-11 22:15:02.035402      6    24   11    22  
3 -118.496048 2019-06-11 22:15:02.035402      6    24   11    22  
4 -118.496020 2019-06-11 22:15:02.035402      6    24   11    22

In [263]:
#34.024212, -118.496475
def generateBaseMap(default_location=[34.024212, -118.496475], default_zoom_start=12):
    base_map = folium.Map(location=default_location, control_scale=True, zoom_start=default_zoom_start)
    return base_map

In [264]:
santa_monica = generateBaseMap()
santa_monica

In [265]:
from folium.plugins import HeatMap
heatmap_bird = bird_data.copy()
heatmap_bird['count'] = 1
base_map = generateBaseMap()
HeatMap(data=heatmap_bird[['latitude', 'longitude', 'count']].groupby(['latitude', 'longitude']).sum().reset_index().values.tolist(), radius=8, max_zoom=13).add_to(base_map)


In [266]:
base_map

In [267]:
#Adding the functionality for us to add markers to the map by clicking on the location where we would like to add the marker
base_map.add_child(folium.ClickForMarker(popup='Potential Location'))

In [268]:
hour_list = []
for hour in heatmap_bird.hour.sort_values().unique():
    hour_list.append(heatmap_bird.loc[heatmap_bird.hour == hour, ['latitude', 'longitude', 'count']].groupby(['latitude', 'longitude']).sum().reset_index().values.tolist())

In [269]:
from folium.plugins import HeatMapWithTime
base_map = generateBaseMap(default_zoom_start=11)
HeatMapWithTime(hour_list, radius=5, gradient={0.2: 'blue', 0.4: 'lime', 0.6: 'orange', 1: 'red'}, min_opacity=0.5, max_opacity=0.8, use_local_extrema=True).add_to(base_map)
base_map

In [273]:
# m = Map()
# HeatMapWithTime(data1).add_to(m)
base_map.add_child(folium.LayerControl())
base_map.save(os.path.join('./bird-view/results', 'heatmap_santamonica_bird.html'))

In [280]:
from fbprophet import Prophet

ModuleNotFoundError: No module named 'fbprophet'